In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/binku-man/bengali_train_sample_final.csv
/kaggle/input/bangla-newspaper-dataset/data_v2/data_v2.json
/kaggle/input/bangla-newspaper-dataset/data/data.json


In [2]:
#loading the training dataset
df = pd.read_json("/kaggle/input/bangla-newspaper-dataset/data_v2/data_v2.json",encoding ='utf-8')

#Preview of training dataset
df.head()

author    category          category_bn        published_date  \
0  গাজীপুর প্রতিনিধি  bangladesh             বাংলাদেশ  ০৪ জুলাই ২০১৩, ২৩:২৬   
1       অনলাইন ডেস্ক      sports                 খেলা  ০৪ জুলাই ২০১৩, ২৩:০৯   
2   নিজস্ব প্রতিবেদক  bangladesh             বাংলাদেশ  ০৪ জুলাই ২০১৩, ২২:২৫   
3       অনলাইন ডেস্ক  technology  বিজ্ঞান ও প্রযুক্তি  ০৪ জুলাই ২০১৩, ২১:৩৭   
4       অনলাইন ডেস্ক  technology  বিজ্ঞান ও প্রযুক্তি  ০৪ জুলাই ২০১৩, ২১:৩৫   

      modification_date          tag comment_count  \
0  ০৪ জুলাই ২০১৩, ২৩:২৭    [গাজীপুর]             0   
1  ০৪ জুলাই ২০১৩, ২৩:১১      [টেনিস]             0   
2  ০৪ জুলাই ২০১৩, ২৩:১২    [রাজনীতি]             0   
3  ০৪ জুলাই ২০১৩, ২১:৪৫     [গবেষণা]             0   
4  ০৪ জুলাই ২০১৩, ২১:৩৭  [কম্পিউটার]             0   

                                               title  \
0  কালিয়াকৈরে টিফিন খেয়ে ৫০০ শ্রমিক অসুস্থ, বিক...   
1              সেমিফাইনাল বাধাও পেরিয়ে গেলেন লিসিকি   
2           সংসদে খালেদার অভিযোগের জবাব দিয়েছে ভারত   
3                               পাসওয়ার্ড ভুলে যান!   
4                             চলে গেলেন মাউস উদ্ভাবক   

                                                 url  \
0  http://www.prothom-alo.com/bangladesh/article/...   
1    http://www.prothom-alo.com/sports/article/19028   
2  http://www.prothom-alo.com/bangladesh/article/...   
3  http://www.prothom-alo.com/technology/article/...   
4  http://www.prothom-alo.com/technology/article/...   

                                             content  
0  গাজীপুরের কালিয়াকৈর উপজেলার তেলিরচালা এলাকায়...  
1  এবারের উইম্বলডনটা স্মরণীয় করে রাখার মিশনেই যে...  
2  জাতীয় সংসদে বিএনপি চেয়ারপারসন ও বিরোধীদলীয় ...  
3  সহজ পাসওয়ার্ডের কারণে অনলাইন অ্যাকাউন্ট সহজেই...  
4  কম্পিউটার মাউসের উদ্ভাবক ডগলাস অ্যাঙ্গেলবার্ট ...

In [3]:
#Removing category equal to bangladesh and international
df = df[(df['category'] != 'bangladesh')] 
df = df[(df['category'] != 'international')]

In [4]:
#Selecting rows randomly from the training dataset
df = df.sample(n=1127,random_state=42)

In [5]:
#Checking Shape of the final dataset
df.shape

(1127, 10)

In [6]:
#printing unique categories in the dataset
print(df['category'].unique())


['economy' 'life-style' 'entertainment' 'sports' 'education' 'opinion'
 'technology']


In [7]:
#printing the frequency of category of the content
df['category'].value_counts()

sports           377
entertainment    235
economy          143
opinion          109
life-style        93
technology        89
education         81
Name: category, dtype: int64

In [8]:
#Removing the numerical values from the content
df.content = df.content.str.replace('\d+',' ')

/tmp/ipykernel_23/204914307.py:2: FutureWarning: The default value of regex will change from True to False in a future version.
  df.content = df.content.str.replace('\d+',' ')


In [9]:
#Replacing the categories of the content with numerical values

df.category = df.category.replace('sports', 1)
df.category = df.category.replace('technology', 2)
df.category = df.category.replace('entertainment', 3)
df.category = df.category.replace('economy', 4)
df.category = df.category.replace('life-style', 5)
df.category = df.category.replace('opinion', 6)
df.category = df.category.replace('education', 7)

df.category.head()

90054     4
401157    5
354857    3
341997    1
75793     3
Name: category, dtype: int64

In [10]:
#Removing punctuations from the dataset

import re
whitespace = re.compile(u"[\s\u0020\u00a0\u1680\u180e\u202f\u205f\u3000\u2000-\u200a]+", re.UNICODE)
bangla_fullstop = u"\u0964"
punctSeq   = u"['\"“”‘’]+|[.?!,…]+|[:;]+"
punc = u"[(),$%^&*+={}\[\]:\"|\'\~`<>/,¦!?½£¶¼©⅐⅑⅒⅓⅔⅕⅖⅗⅘⅙⅚⅛⅜⅝⅞⅟↉¤¿º;-]+"

def remove_punct(t1):
    #t1 ="সৌতিরুবাচ।   তেষু তত্রোপবিষ্টেষু ব্রাহ্মণেষু মহাত্মসু। রুরুশ্চুক্রোশ গহনং বনং গৎবাঽতিদুঃখিতঃ॥   শোকেনাভিহতঃ সোঽথ বিলপন্করুণং বহু। অব্রবীদ্বচনং শোচন্প্রিয়াং স্মৃৎবা প্রমদ্বরাম্॥   শেতে সা ভুবি তন্বঙ্গী মম শোকবিবর্ধিনী। `প্রাণানপহরন্তীব পূর্ণচন্দ্রনিভাননা॥   যদি পীনায়তশ্রোণী পদ্মপত্রনিভেক্ষণা। মুমূর্ষুরপি মে প্রাণানাদায়াশু গমিষ্যতি॥   পিতৃমাতৃসখীনাং চ লুপ্তপিণ্ডস্য তস্য মে।' বান্ধবানাং চ সর্বেষাং কিং নু দুঃখমতঃপরম্॥   যদি দত্তং তপস্তপ্তং গুরবো বা ময়া যদি। সম্যগারাধিতাস্তেন সংজীবতু মম প্রিয়া॥   যথা চ জন্মপ্রভৃতি যতাত্মাঽহং ধৃতব্রতঃ। প্রমদ্বরা তথাদ্যৈষা সমুত্তিষ্ঠতু ভামিনী॥   [এবং লালপ্যতস্তস্য ভার্যার্থে দুঃখিতস্য চ। দেবদূতস্তদাঽভ্যেত্য বাক্যমাহ রুরুং বনে॥]   `কৃষ্ণে বিষ্ণৌ হৃষীকেশে লোকেশেঽসুরবিদ্বিষি। যদি মে নিশ্চলা ভক্তির্মম জীবতু সা প্রিয়া॥   বিলপ্যমানে তু রুরৌ সর্বে দেবাঃ কৃপান্বিতাঃ। দূতং প্রস্থাপয়ামাসুঃ সংদিশ্যাস্য হিতং বচঃ॥   স দূতস্ৎবরিতোঽভ্যেত্য দেবানাং প্রিয়কৃচ্ছুচিঃ। উবাচ দেববচনং রুরুমাভাষ্য দুঃখিতম্॥   দেবৈঃ সর্বৈরহং ব্রহ্মন্প্রেষিতোঽস্মি তবান্তিকম্। ৎবদ্ধিতং ৎবদ্ধিতৈরুক্তং শৃণু বাক্যং দ্বিজোত্তম॥'   অভিধৎসে হ যদ্বাচা রুরো দুঃখান্ন তন্মৃষা। ন তু মর্ত্যস্য ধর্মাত্মন্নায়ুরস্তি গতায়ুষঃ॥   গতায়ুরেষা কৃপণা গন্ধর্বাপ্সরসোঃ সুতা। তস্মাচ্ছোকে মনস্তাত মা কৃথাস্ৎবং কথংচন॥   উপায়শ্চাত্র বিহিতঃ পূর্বং দেবৈর্মহাত্মভিঃ। তং যদীচ্ছসি কর্তুং ৎবং প্রাপ্স্যসীহ প্রমদ্বরাম্॥   রুরুরুবাচ।   ক উপায়ঃ কৃতো দেবৈর্বূহি তত্ৎবেন খেচর। করিষ্যেঽহং তথা শ্রুৎবা ত্রাতুমর্হতি মাং ভবান্॥   দেবেদূত উবাচ।   আয়ুষোঽর্ধং প্রয়চ্ছ ৎবং কন্যায়ৈ ভৃগুনন্দন। এবমুত্থাস্যতি রুরো তব ভার্যা প্রয়দ্বরা॥   রুরুরুবাচ।   আয়ুষোঽর্ধং প্রয়চ্ছামি কন্যায়ৈ খেচরোত্তম। শৃঙ্গাররূপাভরণা সমুত্তিষ্ঠতু মে প্রিয়া॥   সৌতিরুবাচ।   ততো গন্ধর্বরাজশ্চ দেবদূতশ্চ সত্তমৌ। ধর্মরাজমুপেত্যেদং বচনং প্রত্যভাষতাম্॥   ধর্মরাজায়ুষোঽর্ধেন রুরোর্ভার্যা প্রমদ্বরা। সমুত্তিষ্ঠতু কল্যাণী মৃতৈবং যদি মন্যসে॥   ধর্মরাজ উবাচ।   প্রমদ্বরা রুরোর্ভার্যা দেবদূত যদীচ্ছসি। উত্তিষ্ঠৎবায়ুষোঽর্ধেন রুরোরেব সমন্বিতা॥   সৌতিরুবাচ।   এবমুক্তে ততঃ কন্যা সোদতিষ্ঠৎপ্রমদ্বরা। রুরোস্তস্যায়ুষোঽর্ধেন সুপ্তেব বরবর্ণিনী॥   এতদ্দৃষ্টং ভবিষ্যে হি রুরোরুত্তমতেজসঃ। আয়ুষোঽতিপ্রবৃদ্ধস্য ভার্যার্থেঽর্ধমলুপ্যত॥   তত ইষ্টেঽহনি তয়োঃ পিতরৌ চক্রতুর্মুদা। বিবাহং তৌ চ রেমাতে পরস্পরহিতৈষিণৌ॥   স লব্ধ্বা দুর্লভাং ভার্যাং পদ্মকিঞ্জল্কসুপ্রভাম্। ব্রতং চক্রে বিনাশায় জিহ্মগানাং ধৃতব্রতঃ॥   স দৃষ্ট্বা জিহ্মগান্সর্বাংস্তীব্রকোপসমন্বিতঃ। অভিহন্তি যথাসত্ৎবং গৃহ্য প্রহরণং সদা॥   স কদাচিদ্বনং বিপ্রো রুরুরভ্যাগমন্মহৎ। শয়ানং তত্র চাপশ্যড্ডুণ্ডুভং বয়সান্বিতম্॥   তত উদ্যম্য দম্ডং স কালদণ্ডোপমং তদা। জিঘাংসুঃ কুপিতো বিপ্রস্তমুবাচাথ ডুণ্ডুভঃ॥   নাপরাধ্যামি তে কিংচিদহমদ্য তপোধন। সংরম্ভাচ্চ কিমর্থং মামভিহংসি রুষান্বিতঃ॥ ॥   ইতি শ্রীমন্মহাভারতে আদিপর্বাণি পৌলোমপর্বণি নবমোঽধ্যায়ঃ॥  ॥"
    t1= whitespace.sub(" ",t1).strip()
    t1 = re.sub(punctSeq, " ", t1)
    t1 = re.sub(bangla_fullstop, " ",t1)
    t1 = re.sub(punc, " ", t1)
    return t1

df['content']=df['content'].apply(lambda x: remove_punct(x))

df.head()

author  category category_bn              published_date  \
90054     জাহাঙ্গীর শাহ্         4    অর্থনীতি   ০২ সেপ্টেম্বর ২০১৪, ০০:০১   
401157       অনার্য তাপস         5    জীবনযাপন           ০৮ মে ২০১৯, ১১:৩৭   
354857  বিনোদন প্রতিবেদক         3      বিনোদন  ১৩ ফেব্রুয়ারি ২০১৮, ১৩:৩৭   
341997        খেলা ডেস্ক         1        খেলা      ২২ অক্টোবর ২০১৭, ১৮:৪৬   
75793           নাইস নূর         3      বিনোদন        ০৮ জুলাই ২০১৪, ১৭:১৪   

                 modification_date                                  tag  \
90054    ০২ সেপ্টেম্বর ২০১৪, ০০:০১                            [বাণিজ্য]   
401157           ০৮ মে ২০১৯, ১১:৪১  [সম্পর্ক, অধুনা, রবীন্দ্রনাথ ঠাকুর]   
354857  ১৩ ফেব্রুয়ারি ২০১৮, ১৩:৪১                              [সংগীত]   
341997      ২২ অক্টোবর ২০১৭, ১৮:৪৯                            [ক্রিকেট]   
75793         ০৮ জুলাই ২০১৪, ১৭:১৬                              [আলাপন]   

       comment_count                              title  \
90054              0                 ‘বদি আলম’দের বিদায়   
401157             0       অভিমানী রবীন্দ্রনাথের কান্না   
354857             0      সমরজিৎ রায়ের ‘জ্যোৎস্না রাতে’   
341997            ২৫  ‘পাকিস্তানের বোলিং এখন বিশ্বসেরা’   
75793              ১  আমার স্বপ্নের নায়িকা মৌসুমী: নিলয়   

                                                      url  \
90054   http://www.prothom-alo.com/economy/article/307573   
401157  http://www.prothom-alo.com/life-style/article/...   
354857  http://www.prothom-alo.com/entertainment/artic...   
341997  http://www.prothom-alo.com/sports/article/1349531   
75793   http://www.prothom-alo.com/entertainment/artic...   

                                                  content  
90054   দেশের সব কাস্টম হাউস থেকে  বদি আলম দের বিদায় ক...  
401157  অভিমান—সে বড় আজব জিনিস  যত বিখ্যাত  যত তারকা  ...  
354857  গত রোববার রাতে ধানমন্ডির একটি রেস্তোরাঁয় প্রকা...  
341997  বেশ কয়েক দিন ধরেই ভালো ক্রিকেট খেলছে পাকিস্তান...  
75793   মডেল ও অভিনেতা নিলয়  নাটক  বিজ্ঞাপনচিত্রের পাশ...

In [11]:
#installing bnlp_toolkit
!pip install bnlp_toolkit
#Applying tokenization to the dataset
from bnlp import BasicTokenizer
basic_t = BasicTokenizer()
df['content']=df['content'].apply(lambda x: basic_t.tokenize(x))

df.head()

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.1/53.1 kB 4.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 175.4/175.4 kB 9.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... - \ done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 993.5/993.5 kB 37.5 MB/s eta 0:00:00
  Created wheel for emoji: filename=emoji-1.7.0-py3-none-any.whl size=171046 sha256=20352bc4339324f64fdc4811f97013d218bc561edee38794e732f50460691164
  Stored in directory: /root/.cache/pip/wheels/31/8a/8c/315c9e5d7773f74b33d5ed33f075b49c6eaeb7cedbb86e2cf8
Successfully built emoji
  Attempting uninstall: emoji
    Found existing installation: emoji 2.5.0
    Uninstalling emoji-2.5.0:
      Successfully uninstalled emoji-2.5.0


author  category category_bn              published_date  \
90054     জাহাঙ্গীর শাহ্         4    অর্থনীতি   ০২ সেপ্টেম্বর ২০১৪, ০০:০১   
401157       অনার্য তাপস         5    জীবনযাপন           ০৮ মে ২০১৯, ১১:৩৭   
354857  বিনোদন প্রতিবেদক         3      বিনোদন  ১৩ ফেব্রুয়ারি ২০১৮, ১৩:৩৭   
341997        খেলা ডেস্ক         1        খেলা      ২২ অক্টোবর ২০১৭, ১৮:৪৬   
75793           নাইস নূর         3      বিনোদন        ০৮ জুলাই ২০১৪, ১৭:১৪   

                 modification_date                                  tag  \
90054    ০২ সেপ্টেম্বর ২০১৪, ০০:০১                            [বাণিজ্য]   
401157           ০৮ মে ২০১৯, ১১:৪১  [সম্পর্ক, অধুনা, রবীন্দ্রনাথ ঠাকুর]   
354857  ১৩ ফেব্রুয়ারি ২০১৮, ১৩:৪১                              [সংগীত]   
341997      ২২ অক্টোবর ২০১৭, ১৮:৪৯                            [ক্রিকেট]   
75793         ০৮ জুলাই ২০১৪, ১৭:১৬                              [আলাপন]   

       comment_count                              title  \
90054              0                 ‘বদি আলম’দের বিদায়   
401157             0       অভিমানী রবীন্দ্রনাথের কান্না   
354857             0      সমরজিৎ রায়ের ‘জ্যোৎস্না রাতে’   
341997            ২৫  ‘পাকিস্তানের বোলিং এখন বিশ্বসেরা’   
75793              ১  আমার স্বপ্নের নায়িকা মৌসুমী: নিলয়   

                                                      url  \
90054   http://www.prothom-alo.com/economy/article/307573   
401157  http://www.prothom-alo.com/life-style/article/...   
354857  http://www.prothom-alo.com/entertainment/artic...   
341997  http://www.prothom-alo.com/sports/article/1349531   
75793   http://www.prothom-alo.com/entertainment/artic...   

                                                  content  
90054   [দেশের, সব, কাস্টম, হাউস, থেকে, বদি, আলম, দের,...  
401157  [অভিমান, —, সে, বড়, আজব, জিনিস, যত, বিখ্যাত, য...  
354857  [গত, রোববার, রাতে, ধানমন্ডির, একটি, রেস্তোরাঁয়...  
341997  [বেশ, কয়েক, দিন, ধরেই, ভালো, ক্রিকেট, খেলছে, প...  
75793   [মডেল, ও, অভিনেতা, নিলয়, নাটক, বিজ্ঞাপনচিত্রের...

In [12]:
#installing advertools library
!pip install advertools

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 310.0/310.0 kB 10.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 277.2/277.2 kB 22.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 69.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 247.0/247.0 kB 21.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 93.3/93.3 kB 9.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 74.6/74.6 kB 6.9 MB/s eta 0:00:00


In [13]:
#importing the stopwords of bengali
import advertools as adv
adv.stopwords.keys()

dict_keys(['arabic', 'azerbaijani', 'bengali', 'catalan', 'chinese', 'croatian', 'danish', 'dutch', 'english', 'finnish', 'french', 'german', 'greek', 'hebrew', 'hindi', 'hungarian', 'indonesian', 'irish', 'italian', 'japanese', 'kazakh', 'nepali', 'norwegian', 'persian', 'polish', 'portuguese', 'romanian', 'russian', 'sinhala', 'spanish', 'swedish', 'tagalog', 'tamil', 'tatar', 'telugu', 'thai', 'turkish', 'ukrainian', 'urdu', 'vietnamese'])

In [14]:
stop_words=sorted(adv.stopwords['bengali'])

In [15]:
#Function for removing stopwords
def remove_stopwords(text):
  words = [w for w in text if w not in set(stop_words)]
  return words

df['content']=df['content'].apply(lambda x:remove_stopwords(x))


df.content.head()

90054     [কাস্টম, হাউস, বদি, আলম, দের, বিদায়, প্রক্রিয়া...
401157    [অভিমান, —, বড়, আজব, জিনিস, বিখ্যাত, তারকা, বর...
354857    [গত, রোববার, রাতে, ধানমন্ডির, রেস্তোরাঁয়, প্রক...
341997    [ধরেই, ভালো, ক্রিকেট, খেলছে, পাকিস্তান, চ্যাম্...
75793     [মডেল, অভিনেতা, নিলয়, নাটক, বিজ্ঞাপনচিত্রের, প...
Name: content, dtype: object

In [16]:
#installing bangla-stemmer library for stemming the words
!pip install bangla-stemmer

In [17]:
#Applying Stemming to the dataset
from bangla_stemmer.stemmer import stemmer
stmr = stemmer.BanglaStemmer()


def Stemmer(text):
    stem_text = " ".join([stmr.stem(i) for i in text])
    return stem_text

df['content'] = df['content'].apply(lambda x:Stemmer(x))
   

applied fourth rules..
applied first rules..
applied fourth rules..
applied fourth rules..
applied first rules..
applied fourth rules..
applied first rules..
applied fourth rules..
applied first rules..
applied second rules..
applied fourth rules..
applied first rules..
applied first rules..
applied first rules..
applied first rules..
applied second rules..
applied fourth rules..
applied first rules..
applied fourth rules..
applied fourth rules..
applied fourth rules..
applied fourth rules..
applied first rules..
applied fourth rules..
applied first rules..
applied second rules..
applied fourth rules..
applied first rules..
applied first rules..
applied first rules..
applied fourth rules..
applied fourth rules..
applied first rules..
applied first rules..
applied first rules..
applied first rules..
applied first rules..
applied fourth rules..
applied fourth rules..
applied first rules..
applied fourth rules..
applied first rules..
applied fourth rules..
applied second rules..
applied f

In [18]:
df.content.head()

90054     কাস্টম হাউস বদি আলম দের বিদায় প্রক্রিয়া বদি আল...
401157    অভিমান — বড় আজব জিন বিখ্যাত তারকা বরেণ্য মন গহ...
354857    গত রোবব রাত ধানমন্ডির রেস্তোরাঁয় প্রকাশিত সংগী...
341997    ধরে ভালো ক্রিকেট খেল পাকিস্তান চ্যাম্পিয়নস ট্র...
75793     মডেল অভিনেতা নিলয় নাটক বিজ্ঞাপনচিত্র পাশাপাশি ...
Name: content, dtype: object

In [19]:
# creating the Bag of Words model
corpus = []
corpus = df['content']
from sklearn.feature_extraction.text import CountVectorizer
cv = CountVectorizer(max_features = 1200,lowercase=False)
X = cv.fit_transform(corpus).toarray()
y = df.category.values

In [20]:
type(corpus)

pandas.core.series.Series

In [21]:
#Printing the training(features) dataset
print(X)

[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]


In [22]:
#Printing the target variable or class labels
print(y)

[4 5 3 ... 5 1 1]


In [23]:
#splitting training and test dataset
from sklearn.model_selection import train_test_split
X_train,X_test,y_train,y_test = train_test_split(X,y,test_size=0.2,random_state=0)

In [24]:
# training the Naive Bayes Classification model to the training dataset
from sklearn.naive_bayes import GaussianNB
classifier = GaussianNB()
classifier.fit(X_train,y_train)

GaussianNB()

In [25]:
# predicting the values classified by the following model
y_pred = classifier.predict(X_test)

In [26]:
#importing library for evaluation of prediction made by classification model
from sklearn.metrics import accuracy_score,confusion_matrix

# Calculate accuracy
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

# Calculate confusion matrix
confusion_mat = confusion_matrix(y_test, y_pred)
print("Confusion Matrix:\n", confusion_mat)


Accuracy: 0.6371681415929203
Confusion Matrix:
 [[61  2  4  2  2  2  1]
 [ 3  6  3  1  1  2  0]
 [ 1  0 29  2  5  3  0]
 [ 1  2  1 16  0  8  0]
 [ 1  0  5  1  4  9  0]
 [ 0  1  3  3  1 15  0]
 [ 0  0  1  2  3  6 13]]


In [27]:
#Importing Mahabharata dataset in bengali
data = pd.read_csv("/kaggle/input/binku-man/bengali_train_sample_final.csv")
data.head()

Text
0  সঞ্জয় বললেন, "তারপর, হে রাজা, যুদ্ধে অজেয় পর...
1  "ভীষ্ম বললেন, 'সেখানে ঋষিরা, পিত্রী ও দেবতাদের...
2  Sanjaya said,--"Beholding Dhananjaya then to t...
3  ধৃতরাষ্ট্র বললেন, 'হে মহাজ্ঞানী, উচ্চাভিলাষী ব...
4  যুধিষ্ঠির বললেন, হে পরাক্রমশালী অস্ত্রের অধিকা...

In [28]:
#Preprocessing dataset before applying classification model 
data.Text = data.Text.str.replace('\d+',' ')
data['Text']=data['Text'].apply(lambda x: remove_punct(x))
data['Text']=data['Text'].apply(lambda x: basic_t.tokenize(x))
data['Text']=data['Text'].apply(lambda x:remove_stopwords(x))
data['Text']=data['Text'].apply(lambda x:Stemmer(x))

corpus_1=[]
corpus_1=data['Text']

Test_t = cv.fit_transform(corpus_1).toarray()


/tmp/ipykernel_23/2144139888.py:2: FutureWarning: The default value of regex will change from True to False in a future version.
  data.Text = data.Text.str.replace('\d+',' ')


applied first rules..
applied first rules..
applied fourth rules..
applied fourth rules..
applied first rules..
applied third rules..
applied fourth rules..
applied fourth rules..
applied first rules..
applied fourth rules..
applied fourth rules..
applied fourth rules..
applied third rules..
applied fourth rules..
applied first rules..
applied fourth rules..
applied fourth rules..
applied fourth rules..
applied fourth rules..
applied fourth rules..
applied fourth rules..
applied fourth rules..
applied first rules..
applied fourth rules..
applied fourth rules..
applied first rules..
applied fourth rules..
applied first rules..
applied fourth rules..
applied fourth rules..
applied first rules..
applied first rules..
applied fourth rules..
applied second rules..
applied fourth rules..
applied first rules..
applied fourth rules..
applied fourth rules..
applied first rules..
applied fourth rules..
applied first rules..
applied third rules..
applied fourth rules..
applied first rules..
appli

In [29]:
#predicting the results
y_pred_bengali = classifier.predict(Test_t)

In [30]:
print(y_pred_bengali)

[1 1 1 1 1 1 6 6 3 1 6 1 1 6 1 3 6 1 1 1 1 6 6 1 1 1 1 1 7 1 6 1 1 6 1 6 6
 6 1 1 1 6 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 6 1 1 6 1 6 6 6 1 1 6 1 1 6 1 1 1
 1 1 1 6 6 1 1 6 1 1 1 6 1 1 6 1 1 1 1 1 1 6 1 1 6 6]
